In [149]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

In [150]:
df = pd.read_csv('hmeq.csv')

In [151]:
from ydata_profiling import ProfileReport

In [152]:
ProfileReport(train)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 13/13 [00:00<00:00, 492.59it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Khi thấy dữ liệu mất cân bằng như thế này, bạn có thể cân nhắc:

Resampling: Dùng kỹ thuật oversampling (SMOTE) hoặc undersampling để cân bằng dữ liệu.

Thay đổi thuật toán: Dùng các mô hình nhạy cảm với mất cân bằng như XGBoost, hoặc gán trọng số cho các lớp.

Đánh giá bằng F1-score hoặc AUC, chứ không chỉ accuracy.

In [153]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

In [154]:
import statsmodels
import re

In [155]:
from sklearn.preprocessing import MinMaxScaler, LabelEncoder, OneHotEncoder

In [156]:
from sklearn.model_selection import train_test_split

In [157]:
from imblearn.over_sampling import SMOTE
from sklearn.linear_model import LogisticRegression
from sklearn import metrics
from sklearn.metrics import confusion_matrix, accuracy_score, classification_report, f1_score
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import GridSearchCV

In [158]:
from sklearn.tree import DecisionTreeClassifier

In [159]:
from xgboost import XGBClassifier

In [160]:
from sklearn.naive_bayes import GaussianNB
from sklearn.naive_bayes import MultinomialNB
from sklearn.naive_bayes import BernoulliNB
from sklearn.naive_bayes import CategoricalNB

In [161]:
from sklearn.metrics import mean_squared_error
from sklearn.metrics import roc_auc_score


In [162]:
import pandas.core.algorithms as algos
import scipy.stats.stats as stats
import traceback
import string

In [163]:
import scorecardpy as sc

In [164]:
import mlxtend

In [165]:
pd.set_option('display.max_columns', None) 
pd.set_option('display.max_colwidth', None)

In [166]:
df.head()

BAD  LOAN  MORTDUE     VALUE   REASON     JOB   YOJ  DEROG  DELINQ  \
0    1  1100  25860.0   39025.0  HomeImp   Other  10.5    0.0     0.0   
1    1  1300  70053.0   68400.0  HomeImp   Other   7.0    0.0     2.0   
2    1  1500  13500.0   16700.0  HomeImp   Other   4.0    0.0     0.0   
3    1  1500      NaN       NaN      NaN     NaN   NaN    NaN     NaN   
4    0  1700  97800.0  112000.0  HomeImp  Office   3.0    0.0     0.0   

        CLAGE  NINQ  CLNO  DEBTINC  
0   94.366667   1.0   9.0      NaN  
1  121.833333   0.0  14.0      NaN  
2  149.466667   1.0  10.0      NaN  
3         NaN   NaN   NaN      NaN  
4   93.333333   0.0  14.0      NaN

In [167]:
df[['BAD']].value_counts(normalize=True)

BAD
0      0.800503
1      0.199497
Name: proportion, dtype: float64

In [168]:
df

BAD   LOAN  MORTDUE     VALUE   REASON     JOB   YOJ  DEROG  DELINQ  \
0       1   1100  25860.0   39025.0  HomeImp   Other  10.5    0.0     0.0   
1       1   1300  70053.0   68400.0  HomeImp   Other   7.0    0.0     2.0   
2       1   1500  13500.0   16700.0  HomeImp   Other   4.0    0.0     0.0   
3       1   1500      NaN       NaN      NaN     NaN   NaN    NaN     NaN   
4       0   1700  97800.0  112000.0  HomeImp  Office   3.0    0.0     0.0   
...   ...    ...      ...       ...      ...     ...   ...    ...     ...   
5955    0  88900  57264.0   90185.0  DebtCon   Other  16.0    0.0     0.0   
5956    0  89000  54576.0   92937.0  DebtCon   Other  16.0    0.0     0.0   
5957    0  89200  54045.0   92924.0  DebtCon   Other  15.0    0.0     0.0   
5958    0  89800  50370.0   91861.0  DebtCon   Other  14.0    0.0     0.0   
5959    0  89900  48811.0   88934.0  DebtCon   Other  15.0    0.0     0.0   

           CLAGE  NINQ  CLNO    DEBTINC  
0      94.366667   1.0   9.0        NaN  
1     121.833333   0.0  14.0        NaN  
2     149.466667   1.0  10.0        NaN  
3            NaN   NaN   NaN        NaN  
4      93.333333   0.0  14.0        NaN  
...          ...   ...   ...        ...  
5955  221.808718   0.0  16.0  36.112347  
5956  208.692070   0.0  15.0  35.859971  
5957  212.279697   0.0  15.0  35.556590  
5958  213.892709   0.0  16.0  34.340882  
5959  219.601002   0.0  16.0  34.571519  

[5960 rows x 13 columns]

# EDA

In [169]:
print(df.shape)

(5960, 13)


In [170]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5960 entries, 0 to 5959
Data columns (total 13 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   BAD      5960 non-null   int64  
 1   LOAN     5960 non-null   int64  
 2   MORTDUE  5442 non-null   float64
 3   VALUE    5848 non-null   float64
 4   REASON   5708 non-null   object 
 5   JOB      5681 non-null   object 
 6   YOJ      5445 non-null   float64
 7   DEROG    5252 non-null   float64
 8   DELINQ   5380 non-null   float64
 9   CLAGE    5652 non-null   float64
 10  NINQ     5450 non-null   float64
 11  CLNO     5738 non-null   float64
 12  DEBTINC  4693 non-null   float64
dtypes: float64(9), int64(2), object(2)
memory usage: 605.4+ KB


### cat feats - num feats

In [171]:
categorical_features = [col for col in df.columns if df[col].dtype == 'object']
numerical_features = [col for col in df.columns if df[col].dtype != 'object']

print('Number of categorical features:', len(categorical_features))
print('Number of numerical features:', len(numerical_features))

Number of categorical features: 2
Number of numerical features: 11


In [172]:
categorical_features

['REASON', 'JOB']

In [173]:
numerical_features

['BAD',
 'LOAN',
 'MORTDUE',
 'VALUE',
 'YOJ',
 'DEROG',
 'DELINQ',
 'CLAGE',
 'NINQ',
 'CLNO',
 'DEBTINC']

### isnull()

In [174]:
df.isnull().sum().sort_values(ascending=False)

DEBTINC    1267
DEROG       708
DELINQ      580
MORTDUE     518
YOJ         515
NINQ        510
CLAGE       308
JOB         279
REASON      252
CLNO        222
VALUE       112
LOAN          0
BAD           0
dtype: int64

# Fill NaN: Categorical features

In [175]:
# Đếm tần số của từng giá trị trong mỗi feature theo BAD
for feature in categorical_features:
    print(f"\nTần số của {feature} theo BAD:")
    freq_table = pd.crosstab(df[feature], df['BAD'], dropna=False)  # Giữ giá trị NaN nếu có
    print(freq_table)


Tần số của REASON theo BAD:
BAD         0    1
REASON            
DebtCon  3183  745
HomeImp  1384  396
NaN       204   48

Tần số của JOB theo BAD:
BAD         0    1
JOB               
Mgr       588  179
Office    823  125
Other    1834  554
ProfExe  1064  212
Sales      71   38
Self      135   58
NaN       256   23


In [176]:
# Do Debtcon là giá trị phổ biến nhất và tỉ lệ NaN không cao nên ta có thể thay thế NaN bằng Debtcon mà vẫn giữ được phân bổ tổng thể của cột mà không làm thay đổi mối quan hệ với BAD
df['REASON'] = df['REASON'].fillna('DebtCon')

In [177]:
# Tỉ lệ BAD trong NaN là 13/163 = 0.0799
# Office có tỉ lệ BAD thấp nhất, trong khi Other có tỉ lệ BAD cao nhất
# Do đó, thay thế NaN bằng Office nếu NaN nhận BAD = 0, và thay thế bằng Other nếu NaN nhận BAD = 1
df.loc[(df['JOB'].isnull()) & (df['BAD'] == 0), 'JOB'] = 'Office'
df.loc[(df['JOB'].isnull()) & (df['BAD'] == 1), 'JOB'] = 'Other'

for feature in categorical_features:
    print(f"\nTần số của {feature} theo BAD:")
    freq_table = pd.crosstab(df[feature], df['BAD'], dropna=False)  # Giữ giá trị NaN nếu có
    print(freq_table)


Tần số của REASON theo BAD:
BAD         0    1
REASON            
DebtCon  3387  793
HomeImp  1384  396

Tần số của JOB theo BAD:
BAD         0    1
JOB               
Mgr       588  179
Office   1079  125
Other    1834  577
ProfExe  1064  212
Sales      71   38
Self      135   58


# Fill NaN: Numerical Features

In [178]:
# LOAN full nên không cần xử lý
# Bắt đầu với Value
freq_table = pd.crosstab(df['VALUE'], df['BAD'], dropna=False)  # Giữ giá trị NaN nếu có
print(freq_table)

BAD       0    1
VALUE           
8000.0    1    0
8800.0    0    1
9100.0    0    1
9500.0    0    1
11550.0   0    1
...      ..  ...
850000.0  0    1
854112.0  0    1
854114.0  0    1
855909.0  0    1
NaN       7  105

[5382 rows x 2 columns]


In [179]:
df.isnull().sum().sort_values(ascending=False)

DEBTINC    1267
DEROG       708
DELINQ      580
MORTDUE     518
YOJ         515
NINQ        510
CLAGE       308
CLNO        222
VALUE       112
REASON        0
LOAN          0
BAD           0
JOB           0
dtype: int64

In [180]:
# Tỉ lệ missing của VALUE thấp nên điền bằng median là đủ

median_value_bad_0 = df[df['BAD'] == 0]['VALUE'].median()
median_value_bad_1 = df[df['BAD'] == 1]['VALUE'].median()

# Điền giá trị thiếu theo BAD
df.loc[(df['VALUE'].isna()) & (df['BAD'] == 0), 'VALUE'] = median_value_bad_0
df.loc[(df['VALUE'].isna()) & (df['BAD'] == 1), 'VALUE'] = median_value_bad_1

In [181]:
print("Số lượng giá trị thiếu trong VALUE sau khi điền:", df['VALUE'].isna().sum())

Số lượng giá trị thiếu trong VALUE sau khi điền: 0


In [182]:
cols_median_by_bad = ['CLNO', 'YOJ', 'CLAGE', 'NINQ', 'DELINQ', 'DEROG']
for col in cols_median_by_bad:
    df[col] = pd.to_numeric(df[col], errors='coerce')
    median_bad_0 = df[df['BAD'] == 0][col].median()
    median_bad_1 = df[df['BAD'] == 1][col].median()
    df.loc[(df[col].isna()) & (df['BAD'] == 0), col] = median_bad_0
    df.loc[(df[col].isna()) & (df['BAD'] == 1), col] = median_bad_1

In [183]:
features_mortdue = ['CLNO', 'VALUE', 'LOAN', 'BAD', 'MORTDUE']
df_mortdue_impute = df[features_mortdue].copy()

# Đảm bảo chỉ số đồng bộ
df_mortdue_impute.index = df.index

# Xử lý giá trị không phải số
for col in features_mortdue:
    df_mortdue_impute[col] = pd.to_numeric(df_mortdue_impute[col], errors='coerce')

# Kiểm tra NaN trước khi chạy KNN
print("\nSố lượng NaN trong các feature trước khi điền MORTDUE:")
print(df_mortdue_impute.isna().sum())

# Áp dụng KNN Imputer
imputer_mortdue = KNNImputer(n_neighbors=5)
df_mortdue_filled = imputer_mortdue.fit_transform(df_mortdue_impute)

# Chuyển đổi ngược về DataFrame
df_mortdue_filled = pd.DataFrame(df_mortdue_filled, columns=features_mortdue, index=df.index)

# Gán lại giá trị MORTDUE
df['MORTDUE'] = df_mortdue_filled['MORTDUE']

# 4. Kiểm tra số lượng giá trị thiếu sau khi điền
print("\nSố lượng giá trị thiếu trong MORTDUE sau khi điền:", df['MORTDUE'].isna().sum())


Số lượng NaN trong các feature trước khi điền MORTDUE:
CLNO         0
VALUE        0
LOAN         0
BAD          0
MORTDUE    518
dtype: int64

Số lượng giá trị thiếu trong MORTDUE sau khi điền: 0


In [184]:
# 3. Điền DEBTINC bằng KNN Imputation
features_debtinc = ['CLNO', 'MORTDUE', 'NINQ', 'LOAN', 'VALUE', 'BAD', 'DEBTINC']
df_debtinc_impute = df[features_debtinc].copy()

# Đảm bảo chỉ số đồng bộ
df_debtinc_impute.index = df.index

# Xử lý giá trị không phải số
for col in features_debtinc:
    df_debtinc_impute[col] = pd.to_numeric(df_debtinc_impute[col], errors='coerce')

# Kiểm tra NaN trước khi chạy KNN
print("\nSố lượng NaN trong các feature trước khi điền DEBTINC:")
print(df_debtinc_impute.isna().sum())

# Áp dụng KNN Imputer
imputer_debtinc = KNNImputer(n_neighbors=5)
df_debtinc_filled = imputer_debtinc.fit_transform(df_debtinc_impute)

# Chuyển đổi ngược về DataFrame
df_debtinc_filled = pd.DataFrame(df_debtinc_filled, columns=features_debtinc, index=df.index)

# Gán lại giá trị DEBTINC
df['DEBTINC'] = df_debtinc_filled['DEBTINC']

# 4. Kiểm tra số lượng giá trị thiếu sau khi điền
print("\nSố lượng giá trị thiếu trong DEBTINC sau khi điền:", df['DEBTINC'].isna().sum())



Số lượng NaN trong các feature trước khi điền DEBTINC:
CLNO          0
MORTDUE       0
NINQ          0
LOAN          0
VALUE         0
BAD           0
DEBTINC    1267
dtype: int64

Số lượng giá trị thiếu trong DEBTINC sau khi điền: 0


In [185]:
# 1. Lưu DataFrame thành file CSV
df.to_csv('hmeq_filled_data.csv', index=False)
print("Đã lưu dữ liệu vào file 'hmeq_filled_data.csv'.")

Đã lưu dữ liệu vào file 'hmeq_filled_data.csv'.


# TRAINING = Naive Bayes với dữ liệu mất cân bằng:

In [186]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
import numpy as np

# 1. Chuẩn bị dữ liệu
# Giả định cột mục tiêu là 'BAD' và các cột còn lại là đặc trưng
# Lấy danh sách các cột số và phân loại
numeric_cols = ['LOAN', 'MORTDUE', 'VALUE', 'YOJ', 'CLAGE', 'NINQ', 'CLNO', 'DEBTINC', 'DELINQ', 'DEROG']
categorical_cols = ['REASON', 'JOB']

# Kết hợp tất cả cột đặc trưng
feature_cols = numeric_cols + categorical_cols

# Tách đặc trưng (X) và mục tiêu (y)
X = df[feature_cols]
y = df['BAD']

# 2. Mã hóa cột phân loại (One-Hot Encoding)
X = pd.get_dummies(X, columns=categorical_cols, drop_first=True)

# 3. Tách dữ liệu thành tập huấn luyện và tập kiểm tra
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# 4. Khởi tạo và huấn luyện mô hình Naive Bayes
model = GaussianNB()
model.fit(X_train, y_train)

# 5. Dự đoán và đánh giá mô hình
y_pred = model.predict(X_test)

# Tính độ chính xác
accuracy = accuracy_score(y_test, y_pred)
print(f"\nĐộ chính xác của mô hình: {accuracy:.2f}")

# In ma trận nhầm lẫn
conf_matrix = confusion_matrix(y_test, y_pred)
print("\nMa trận nhầm lẫn:")
print(conf_matrix)

# In báo cáo phân loại
print("\nBáo cáo phân loại:")
print(classification_report(y_test, y_pred))

# 6. (Tùy chọn) Xem trước dự đoán
print("\n5 dự đoán đầu tiên trên tập kiểm tra:")
print(pd.DataFrame({'Thực tế': y_test[:5].values, 'Dự đoán': y_pred[:5]}))


Độ chính xác của mô hình: 0.80

Ma trận nhầm lẫn:
[[906  21]
 [222  43]]

Báo cáo phân loại:
              precision    recall  f1-score   support

           0       0.80      0.98      0.88       927
           1       0.67      0.16      0.26       265

    accuracy                           0.80      1192
   macro avg       0.74      0.57      0.57      1192
weighted avg       0.77      0.80      0.74      1192


5 dự đoán đầu tiên trên tập kiểm tra:
   Thực tế  Dự đoán
0        0        0
1        0        0
2        0        0
3        0        0
4        0        0


# SMOTETomek

In [189]:
import pandas as pd
from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import RandomUnderSampler
from imblearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split

# 1. Chuẩn bị dữ liệu
# Lấy danh sách các cột số và phân loại
numeric_cols = ['LOAN', 'MORTDUE', 'VALUE', 'YOJ', 'CLAGE', 'NINQ', 'CLNO', 'DEBTINC', 'DELINQ', 'DEROG']
categorical_cols = ['REASON', 'JOB']
feature_cols = numeric_cols + categorical_cols

# Tách đặc trưng (X) và mục tiêu (y)
X = df[feature_cols]
y = df['BAD']

# Mã hóa cột phân loại (One-Hot Encoding)
X = pd.get_dummies(X, columns=categorical_cols, drop_first=True)

# 2. Cân bằng dữ liệu với SMOTE và RandomUnderSampler
# Định nghĩa pipeline: SMOTE (oversampling) rồi RandomUnderSampler (undersampling)
# Mục tiêu: 2980 BAD = 0 và 2980 BAD = 1
sampling_strategy = {0: 2980, 1: 2980}  # Số lượng mẫu mong muốn cho mỗi lớp
over = SMOTE(sampling_strategy='auto', random_state=42)
under = RandomUnderSampler(sampling_strategy=sampling_strategy, random_state=42)
pipeline = Pipeline(steps=[('over', over), ('under', under)])

# Áp dụng pipeline để cân bằng dữ liệu
X_resampled, y_resampled = pipeline.fit_resample(X, y)

# 3. Tạo DataFrame mới (new_df) từ dữ liệu đã cân bằng
new_df = pd.DataFrame(X_resampled, columns=X.columns)
new_df['BAD'] = y_resampled

# 4. Kiểm tra tỷ lệ lớp sau khi cân bằng
print("Số lượng mẫu trong new_df sau khi cân bằng:")
print(new_df['BAD'].value_counts())

# 5. (Tùy chọn) Xem trước 5 dòng đầu của new_df
print("\n5 dòng đầu của new_df:")
print(new_df.head())

# 6. (Tùy chọn) Lưu new_df thành file để kiểm tra
new_df.to_csv('hmeq_balanced_custom.csv', index=False)
print("\nĐã lưu dữ liệu cân bằng vào file 'hmeq_balanced_custom.csv'.")

Số lượng mẫu trong new_df sau khi cân bằng:
BAD
0    2980
1    2980
Name: count, dtype: int64

5 dòng đầu của new_df:
       LOAN  MORTDUE     VALUE   YOJ       CLAGE  NINQ  CLNO    DEBTINC  \
1346  10600  82365.0  100272.0   3.0  122.483594   0.0  26.0  33.651647   
4701  24800  82670.0  106563.0   8.0  302.984432   2.0  28.0  30.956486   
3363  17900  62697.0   89848.0   7.0  113.058897   0.0  19.0  24.072191   
4989  26400  44333.0   68945.0  18.0  173.495392   2.0  21.0  32.349412   
873    8800  26607.0   39710.0   0.0  104.692825   1.0  30.0  38.326728   

      DELINQ  DEROG  REASON_HomeImp  JOB_Office  JOB_Other  JOB_ProfExe  \
1346     0.0    1.0           False       False      False         True   
4701     0.0    0.0           False       False      False        False   
3363     0.0    0.0           False        True      False        False   
4989     0.0    0.0           False        True      False        False   
873      0.0    0.0            True        True      Fal

In [191]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report

# 1. Chuẩn bị dữ liệu từ new_df
# Tách đặc trưng (X) và mục tiêu (y)
X = new_df.drop('BAD', axis=1)
y = new_df['BAD']

# 2. Tách dữ liệu thành tập huấn luyện và tập kiểm tra
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# 3. Huấn luyện mô hình Naive Bayes
model = GaussianNB()
model.fit(X_train, y_train)

# 4. Dự đoán và đánh giá mô hình
y_pred = model.predict(X_test)

# Tính độ chính xác
accuracy = accuracy_score(y_test, y_pred)
print(f"\nĐộ chính xác của mô hình trên new_df: {accuracy:.2f}")

# In ma trận nhầm lẫn
conf_matrix = confusion_matrix(y_test, y_pred)
print("\nMa trận nhầm lẫn:")
print(conf_matrix)

# In báo cáo phân loại
print("\nBáo cáo phân loại:")
print(classification_report(y_test, y_pred))

# Xem trước 5 dự đoán đầu tiên
print("\n5 dự đoán đầu tiên trên tập kiểm tra:")
print(pd.DataFrame({'Thực tế': y_test[:5].values, 'Dự đoán': y_pred[:5]}))


Độ chính xác của mô hình trên new_df: 0.65

Ma trận nhầm lẫn:
[[551  68]
 [355 218]]

Báo cáo phân loại:
              precision    recall  f1-score   support

           0       0.61      0.89      0.72       619
           1       0.76      0.38      0.51       573

    accuracy                           0.65      1192
   macro avg       0.69      0.64      0.62      1192
weighted avg       0.68      0.65      0.62      1192


5 dự đoán đầu tiên trên tập kiểm tra:
   Thực tế  Dự đoán
0        0        0
1        0        0
2        1        1
3        1        0
4        0        0
